In [0]:
import pandas as pd
import numpy as np

import re
import json

# DSA

In [0]:
df = pd.read_excel("/dbfs/FileStore/google-ai-coaching/DSA/QASA_Form__MY_Teledirect___DSA_Sales___DSA_Sales_5_0_.xlsx", sheet_name="Sheet1")

In [0]:
df.columns = ["category", "Description"] + df.iloc[0, 2:].values.tolist()
df_qaform = df.drop("Note", axis=1)
df_qaform["category"] = df_qaform.shift(1)["category"] + ": " + df_qaform["category"]
df_qaform = df_qaform.dropna(how="any")
df_qaform
qa_form = (df_qaform["category"] + "\n" + df_qaform["Description"] 
 + "\n\n" + "Good:\n" + df_qaform["Good"] 
 + "\n\n" + "Average:\n" + df_qaform["Average"] 
 + "\n\n" + "Needs Improvement:\n" + df_qaform["Needs Improvement"]
 + "\n\n" + "Not Applicable:\n" + df_qaform["Not applicable"]).tolist()

In [0]:
df_qaform.to_csv("/dbfs/FileStore/google-ai-coaching/DSA/preprocessed/df_qaform.csv", index=False)

In [0]:
for form in qa_form:
    print(form)
    print("###############")

# Onboarding

In [0]:
df = pd.read_excel('/dbfs/FileStore/google-ai-coaching/_Scaled_Onboarding__QASA_Forms_.xlsx',
                   sheet_name='PitchOpti Call 2.0 (Q1 23)')
df.head(10)

## Getting the Main Headings

In [0]:
# KEY DECISION: Get the Main Headings by getting all rows with the KSS value

In [0]:
# Create a boolean mask using vectorized operations to match 'KSS' exactly
mask = df.astype(str).eq('KSS').any(axis=1)

# Use the mask to filter the DataFrame
result = df[mask]

# # The 'result' DataFrame now contains rows with 'KSS' in any column as the exact string
# display(result)

main_stages_list = result['Unnamed: 1'].values.tolist()
main_stages_list

## Getting the Stage - Substage Pairs

In [0]:
df

In [0]:
# Initialize variables
stage_substage_dict = {}
current_stage = None

# Iterate through the Series
for item in df['Unnamed: 1']:
    if item is not None:
        # Check if the item is a heading based on your initial list
        if item in main_stages_list:
            current_stage = item
            stage_substage_dict[current_stage] = []
        else:
            # If it's not None and not a heading, it's a subheading
            if current_stage:
                if not pd.isna(item):
                    stage_substage_dict[current_stage].append(item)

print(json.dumps(stage_substage_dict, indent=4))

In [0]:
# Convert the dictionary to a list of tuples
data_list = [(key, value) for key, values in stage_substage_dict.items() for value in values]

# Create a DataFrame from the list
stage_substage_df = pd.DataFrame(data_list, columns=['Stage', 'Sub-stage'])

# Print the DataFrame
display(stage_substage_df)


## Getting the Substage - KSS Pairs

In [0]:
# Get substage and KSS columns only
heading_details = df.loc[:, 'Unnamed: 1': 'Unnamed: 2'].copy()

# Forward fill null values in substage column to do substage: KSS matching
# Necessary due to merged cells in excel file causing null values in pd dataframe
heading_details.loc[:, 'Unnamed: 1'] = heading_details.loc[:, 'Unnamed: 1'].ffill(axis=0)
heading_details.head(10)

In [0]:
# Remove rows containing the main stage (e.g. Opening, Objection Handling)

# Create a boolean mask using vectorized operations to match 'KSS' exactly
mask = heading_details.astype(str).eq('KSS').any(axis=1)

# Use the mask to filter the DataFrame
heading_details = heading_details[~mask].copy()
heading_details.rename(columns={'Unnamed: 1': 'Sub-stage', 'Unnamed: 2': 'KSS'}, inplace=True)
heading_details.head(10)

In [0]:
# Remove irrelevant rows
# Logic here is to remove null rows in KSS column only if the corresponding Substage value is non-unique in its column
# Necessary to prevent removal of substages without any KSS details

df = heading_details

# Step 1: Identify non-unique values in the first column
non_unique_values = df[df['Sub-stage'].duplicated(keep=False) | df['Sub-stage'].duplicated(keep='first')]

# Step 2: Filter rows based on non-unique values in the first column and null values in the second column
filtered_df = df[~((df['Sub-stage'].isin(non_unique_values['Sub-stage'])) & (df['KSS'].isnull()))]

# Now, 'filtered_df' contains the rows where null values in the second column are deleted
display(filtered_df.head(10))


## Merge the collected pairs

In [0]:
# Merge the dataframes
display(stage_substage_df.head())
display(filtered_df.head())

In [0]:
# Check for null
print(stage_substage_df.isnull().sum())
print(filtered_df.isnull().sum())

In [0]:
# merge
df_all = pd.merge(stage_substage_df, filtered_df, on='Sub-stage')
df_all.head(10)

In [0]:
# Check null
df_all.isnull().sum()

In [0]:
# Check for duplicates
df_all.duplicated().sum()

## Text Cleaning

In [0]:
def clean_text(text):
    # Remove leading and trailing spaces
    cleaned_text = text.strip()

    # Remove numbers followed by a period at the start
    cleaned_text = re.sub(r'^\d+\.\s*', '', cleaned_text)

    # Replace number lists like "1." or "1)" with a dash
    cleaned_text = re.sub(r'(\d+[.)])\s*', r'- ', cleaned_text)

    # Add a newline before dash (with conditions; see regex)
    cleaned_text = re.sub(r'(?<=[^\nA-Za-z0-9])([\-])', r'\n\1', cleaned_text)

    # Remove extra newline characters
    cleaned_text = re.sub(r'\n\n+', '\n', cleaned_text)
    
    return cleaned_text


In [0]:
df_all = df_all.applymap(lambda x: clean_text(x) if pd.notna(x) else x)
df_all.head(10)

In [0]:
# Save dataframe
# df_all.to_csv('/dbfs/FileStore/google-ai-coaching/google_extracted_QA_fields.csv')

## Formatting for the prompt

In [0]:
df = df_all.copy()

# Initialize variables to keep track of the current heading and subheading
current_heading = None
current_subheading = None

# Initialize a variable to keep track of subheading letters
subheading_letter = 'A'

# Initialize a variable to keep track of the detail number
detail_number = 1

# Iterate through the DataFrame and format the data
output = []
for _, row in df.iterrows():
    heading = row['Stage']
    subheading = row['Sub-stage']
    detail = row['KSS']

    if heading != current_heading:
        if current_heading is not None:
            output.append('')

        output.append(f'{heading}')
        current_heading = heading
        subheading_letter = 'A'
        detail_number = 1

    if subheading != current_subheading:
        output.append(f'    {subheading_letter}. {subheading}')
        current_subheading = subheading
        subheading_letter = chr(ord(subheading_letter) + 1)
        detail_number = 1

    # Check if detail is not null
    if not pd.isna(detail):
        detail = f'{detail_number}. {detail}'

        if len(detail.splitlines()) > 1:
            # Split the string into lines
            lines = detail.split('\n')

            # Indent lines starting from the second line
            indented_lines = [lines[0]] + [' ' * 11 + line for line in lines[1:]]

            # Join the indented lines back into a single string
            detail = '\n'.join(indented_lines)

        output.append(f'        {detail}')
        detail_number += 1

# Join the formatted output into a single string
formatted_output = '\n'.join(output)
print(formatted_output)
